In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
import os
os.chdir('/content/drive/MyDrive')

<h1 style="color:red">Importing Libiraries</h1>

In [3]:
import numpy as np
import pandas as pd
import  string
from string import digits
import re
from sklearn.utils import  shuffle
from sklearn.model_selection import train_test_split
from keras.layers import Input,LSTM,Embedding,Dense
from keras.models import Model

import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline

Load The Data

In [4]:
df = pd.read_csv("Hindi_English_Truncated_Corpus.csv")
df.head(2)

source                                   english_sentence  \
0    ted  politicians do not have permission to do what ...   
1    ted         I'd like to tell you about one such child,   

                                      hindi_sentence  
0  राजनीतिज्ञों के पास जो कार्य करना चाहिए, वह कर...  
1  मई आपको ऐसे ही एक बच्चे के बारे में बताना चाहू...

In [5]:
df.columns

Index(['source', 'english_sentence', 'hindi_sentence'], dtype='object')

In [6]:
df["source"].value_counts()

tides        50000
ted          39881
indic2012    37726
Name: source, dtype: int64

Let's take sample data 5000

In [7]:
df =df.sample(40000)

In [8]:
df.shape

(40000, 3)

In [9]:
df.drop("source",axis=1,inplace=True)

In [10]:
df.shape

(40000, 2)

In [11]:
df[df.duplicated()]

english_sentence hindi_sentence
51416       (Laughter)         (हंसी)
24941       (Laughter)         (हँसी)
13344       (Laughter)         (हँसी)
70275       (Laughter)         (हँसी)
71156          context         संदर्भ
...                ...            ...
6192        (Laughter)         (हँसी)
6729     See this also    यह भी देखिए
55540       (Applause)      (तालियाँ)
49232        Beginning          आरम्भ
16980          (Music)        (संगीत)

[552 rows x 2 columns]

In [12]:
len(df[df.duplicated()])

552

In [13]:
df.drop_duplicates(inplace=True)

In [14]:
df.shape

(39448, 2)

In [15]:
5000-4965

35

In [16]:
df.isnull().sum()

english_sentence    0
hindi_sentence      0
dtype: int64

Let Start Cleaning Process

In [17]:
df.reset_index(inplace=True)

In [18]:
df.drop("index",axis=1,inplace=True)

In [19]:
df.head(5)

english_sentence  \
0  Another Rs 1.46 crore arrived in four instalme...   
1       You've got to just respond to the situation.   
2                that the opposite may also be true.   
3                            martial art movements.”   
4                                  South Africa: 222   

                                      hindi_sentence  
0  पाए और मार्च 1995 और नवंबर 1999 के बीच चार किश...  
1   आप केवल परिस्थितियों के अनुसार कार्य कर सकते हैं  
2      बिल्कुल विपरीत सोच भी उतनी ही वैध हो सकती है.  
3                                   भी कर सकता हूँ |  
4                               दक्षिण अफ्रीका : २२२

Data Preprocessing

***English_Text_Preprocessing*** 

In [20]:
# Here we are replacing the words
mispell_dict = {"aren't" : "are not", "can't" : "cannot", "couldn't" : "could not", 
                "couldnt" : "could not", "didn't" : "did not", "doesn't" : "does not", 
                "doesnt" : "does not", "don't" : "do not", "hadn't" : "had not", 
                "hasn't" : "has not", "haven't" : "have not", "havent" : "have not", 
                "he'd" : "he would", "he'll" : "he will", "he's" : "he is", "i'd" : "I would",
                "i'd" : "I had", "i'll" : "I will", "i'm" : "I am", "isn't" : "is not", 
                "it's" : "it is", "it'll":"it will", "i've" : "I have", "let's" : "let us", 
                "mightn't" : "might not", "mustn't" : "must not", "shan't" : "shall not", 
                "she'd" : "she would", "she'll" : "she will", "she's" : "she is", 
                "shouldn't" : "should not", "shouldnt" : "should not", "that's" : "that is", 
                "thats" : "that is", "there's" : "there is", "theres" : "there is", 
                "they'd" : "they would", "they'll" : "they will", "they're" : "they are", 
                "theyre": "they are", "they've" : "they have", "we'd" : "we would", 
                "we're" : "we are", "weren't" : "were not", "we've" : "we have", 
                "what'll" : "what will", "what're" : "what are", "what's" : "what is", 
                "what've" : "what have", "where's" : "where is", "who'd" : "who would",
                "who'll" : "who will", "who're" : "who are", "who's" : "who is", 
                "who've" : "who have", "won't" : "will not", "wouldn't" : "would not", 
                "you'd" : "you would", "you'll" : "you will", "you're" : "you are", 
                "you've" : "you have", "'re": " are", "wasn't": "was not", "we'll":" will", 
                "didn't": "did not", "tryin'":"trying"
                }

def deconcate(sent):
    keys = mispell_dict.keys()
    cleaned_sentence = []
    for word in sent.split(' '):
        if word in keys:
            cleaned_sentence.append(mispell_dict[word])
        else:
            cleaned_sentence.append(word)
    return ' '.join(cleaned_sentence)

In [21]:
#In words also there special symbols like "ans@wer"
def sentences_cleaner(x):
  l=[]
  x=x.lower()
  x=x.split()
  for i in x:
    u =''.join(str(e) for e in i if e not in string.punctuation)
    u=u.strip()
    l.append(u)
  v =' '.join(str(e) for e in l)
  return v

In [22]:
df['english_sentence']=df['english_sentence'].apply(lambda x:re.sub("[^A-Za-z ]","",x))

In [23]:
df['english_sentence']=df['english_sentence'].apply(lambda x:deconcate(x))

In [24]:
df['english_sentence']=df["english_sentence"].apply(lambda x:sentences_cleaner(x))


In [25]:
df["english_sentence"]

0        another rs crore arrived in four instalments b...
1               youve got to just respond to the situation
2                       that the opposite may also be true
3                                    martial art movements
4                                             south africa
                               ...                        
39443    agra is a historic city and its evidences have...
39444      i am becoming a solution provider im very happy
39445    this glacier is km long km wide and almost met...
39446    and forgetting is the necessary result of any ...
39447    just like them all are brothers the sons of bh...
Name: english_sentence, Length: 39448, dtype: object

In [26]:
all_english_words=set()
for senten in df["english_sentence"]:
  for word in senten.split():
    all_english_words.add(word)

In [27]:
all_english_words

{'saunders',
 'fathehpur',
 'negation',
 'praiseworthy',
 'smile',
 'seemed',
 'childish',
 'elaborated',
 'waged',
 'enhancing',
 'preemalakshaana',
 'cataloguing',
 'titallum',
 'selfrepair',
 'spain',
 'high',
 'runsto',
 'chandragupta',
 'khuranarabialkhuranis',
 'sozati',
 'interval',
 'numerical',
 'glamour',
 'jbuar',
 'identical',
 'fought',
 'pushcart',
 'nuptial',
 'dismissive',
 'bhagwatgeeta',
 'robberflies',
 'regardingthe',
 'silt',
 'avoiding',
 'paralysing',
 'sovereignty',
 'mileage',
 'unthinking',
 'epididymis',
 'bigelow',
 'leached',
 'cofounder',
 'unorganized',
 'tipping',
 'lanes',
 'judah',
 'llkhi',
 'turkhud',
 'proficient',
 'kurki',
 'insertion',
 'elytra',
 'practices',
 'sarhind',
 'canal',
 'villages',
 'sajeev',
 'aeronauitcal',
 'impressed',
 'insecurity',
 'parsipur',
 'propertyholders',
 'sharkscientist',
 'unattainable',
 'gazetteers',
 'hunts',
 'blatta',
 'showed',
 'wisdom',
 'predatory',
 'consul',
 'disgrace',
 'dressmakers',
 'dissapointed',
 

In [28]:
len(all_english_words)

38582

***Hindi_Text_Preprocessing*** 

In [29]:
# Converting The Data Into Lowercase
df['hindi_sentence']=df['hindi_sentence'].apply(lambda x: x.lower())

In [30]:
# Removing English Words
df['hindi_sentence']=df['hindi_sentence'].apply(lambda x:re.sub('[A-Za-z]',"",x))

In [31]:
# Removing Punch Symbols like '
df['hindi_sentence']=df['hindi_sentence'].apply(lambda x: re.sub("'", '', x))


In [32]:
# Removing Special Characters
df['hindi_sentence']=df['hindi_sentence'].apply(lambda x: ''.join(ch for ch in x if ch not in string.punctuation))


In [33]:
# Removing Numberical values
remove_digits = str.maketrans('', '', digits)
df['hindi_sentence']=df['hindi_sentence'].apply(lambda x: x.translate(remove_digits))

In [34]:
df['hindi_sentence'] = df['hindi_sentence'].apply(lambda x: re.sub("[२३०८१५७९४६°μ]", "", x))


In [35]:
# Removing Extra empty spaces
df['hindi_sentence']=df['hindi_sentence'].apply(lambda x: x.strip())


In [36]:
# Adding The Start and End To Know the Starting and Ending of sentences
df['hindi_sentence'] = df['hindi_sentence'].apply(lambda x : 'START_ '+ x + ' _END')

In [37]:
all_hindi_words = set()
for sento in df["hindi_sentence"]:
  for word in sento.split():
    all_hindi_words.add(word)

In [38]:
len(all_hindi_words)

44333

In [39]:
all_hindi_words

{'समज्हैते',
 '“नाइजेल',
 'जीप',
 'परआक्सीएसाइल',
 'फ़ैल',
 'बितर',
 'करायायह',
 'हमूदउररहमान',
 'कथासाहित्य',
 'आड़वाणी',
 'पीएलएबी',
 'मनोज',
 'संस्थापक',
 'अर्धसूत्रण',
 'अचरज',
 'स्टड़ीज',
 'लेदर',
 'स्टीवर्ट',
 'करवाएं',
 'सादा',
 'पत्रकारिता',
 'मोड़ना',
 'मरूस्थल',
 'कराऐँगी',
 'रोकेंवह',
 'छोटेबड़ै',
 'वायुमंडलीसय',
 'शिकागो',
 'ग्रीन',
 'टिके',
 'ब्यूरो',
 'चुनीं',
 'धातु',
 'चाहें।',
 'गयीइनमें',
 'जमींदारियां',
 'ঠাকুর',
 'छोड़ेने',
 'फोंस',
 'थीकि',
 'पिचहोनेसे',
 'वैश्वीकृत',
 'राजखोसला',
 'बुटवल',
 'पडोसी',
 'अभिलेखन',
 'इफ़र',
 'ग्रहों',
 'उड़ाते',
 'गांठते',
 'फ़ौजदार',
 'आत्मनिर्भरता',
 'ऐतयार',
 'दार्शनिको',
 'कलेन्डर',
 'घनमीटर',
 'धारणाओं',
 'कॉख',
 'सोचविचार',
 'निर्माणकालजो',
 'हैपहले',
 'चमत्कारः',
 'मिस्ट्री',
 'पिचें',
 'मॉडेम',
 'प्रस्फुटित',
 'झुण्ड',
 'गाँधी',
 'मक्खिया',
 'बाईं',
 'ऋबोस',
 'उद्द्योगिक',
 'ओक्सफ़ोर्ड',
 'नियामत',
 'दाँतों',
 'कार्निसो',
 'कालहस्ती',
 'चार्ट',
 'शताव्दियौं',
 'दुखों',
 'गुफामंदिरों',
 'लार्वे',
 'प्रशंसिका',
 'गुटकों',
 'थेंय

***Adding Extra Length Columns of Every Sentences***

In [40]:
df["Length of English Sentences"]=df['english_sentence'].apply(lambda x:len(x.split(" ")))

In [41]:
df["Length of Hindi Sentences"]=df['hindi_sentence'].apply(lambda x:len(x.split(" ")))

In [42]:
df.head(3)

english_sentence  \
0  another rs crore arrived in four instalments b...   
1         youve got to just respond to the situation   
2                 that the opposite may also be true   

                                      hindi_sentence  \
0  START_ पाए और मार्च  और नवंबर  के बीच चार किश्...   
1  START_ आप केवल परिस्थितियों के अनुसार कार्य कर...   
2  START_ बिल्कुल विपरीत सोच भी उतनी ही वैध हो सक...   

   Length of English Sentences  Length of Hindi Sentences  
0                           11                         17  
1                            8                         11  
2                            7                         12

In [43]:
df[df['Length of English Sentences']>30].shape


(3733, 4)

In [44]:
df=df[df['Length of English Sentences']<=20]
df=df[df['Length of Hindi Sentences']<=20]

In [45]:
df.shape

(25767, 4)

In [46]:
df.head(3)

english_sentence  \
0  another rs crore arrived in four instalments b...   
1         youve got to just respond to the situation   
2                 that the opposite may also be true   

                                      hindi_sentence  \
0  START_ पाए और मार्च  और नवंबर  के बीच चार किश्...   
1  START_ आप केवल परिस्थितियों के अनुसार कार्य कर...   
2  START_ बिल्कुल विपरीत सोच भी उतनी ही वैध हो सक...   

   Length of English Sentences  Length of Hindi Sentences  
0                           11                         17  
1                            8                         11  
2                            7                         12

In [47]:
df.tail(3)

english_sentence  \
39445  this glacier is km long km wide and almost met...   
39446  and forgetting is the necessary result of any ...   
39447  just like them all are brothers the sons of bh...   

                                          hindi_sentence  \
39445  START_ यह हिमनद  किमी लंबा व  किमी चौड़ा और लग...   
39446  START_ और इस प्रकार विस्मरण एक दीर्घकालकई शताब...   
39447  START_ उन्हीं की तरह सभी भाईभाई हैं  भारत माता...   

       Length of English Sentences  Length of Hindi Sentences  
39445                           11                         17  
39446                           20                         14  
39447                           11                         14

# ***Important Items***

***Max _Length :***

In [48]:
max_length_source =max(df['Length of English Sentences'])
max_length_source

20

Maximum Length source [ English ] : 20

In [49]:
max_length_target = max(df['Length of Hindi Sentences'])
max_length_target

20

Maximum Length Target [ Hindi ] : 20

**[ English ] Input Words In sorted order :::**

In [50]:
input_words = sorted(list(all_english_words))
input_words

['a',
 'aa',
 'aaa',
 'aaber',
 'aac',
 'aacharan',
 'aachmanritually',
 'aact',
 'aadam',
 'aadan',
 'aadanthy',
 'aadh',
 'aadi',
 'aadimindian',
 'aadiparva',
 'aaee',
 'aaeene',
 'aag',
 'aagara',
 'aah',
 'aai',
 'aaineakbari',
 'aaj',
 'aak',
 'aakhr',
 'aakrnsa',
 'aalekh',
 'aalh',
 'aalims',
 'aamar',
 'aamir',
 'aamlopi',
 'aananthi',
 'aand',
 'aangghchche',
 'aangkadoong',
 'aanre',
 'aaranyak',
 'aarathi',
 'aarati',
 'aareer',
 'aarsu',
 'aarthie',
 'aarti',
 'aarun',
 'aarya',
 'aathri',
 'aatmikaprikarmasandhiniyamageetparvdeepgeetsmarikaneelambra',
 'aatre',
 'aatri',
 'aawazekhalq',
 'aayaat',
 'aayat',
 'aayats',
 'aaysaar',
 'aazad',
 'aazadhind',
 'aazamgad',
 'ab',
 'abacha',
 'aback',
 'abacus',
 'abad',
 'abandon',
 'abandoned',
 'abandoning',
 'abani',
 'abated',
 'abatement',
 'abattoirs',
 'abbas',
 'abbasi',
 'abbasid',
 'abbasies',
 'abbasis',
 'abbreviated',
 'abc',
 'abcde',
 'abcl',
 'abd',
 'abdel',
 'abdictions',
 'abdomen',
 'abdominal',
 'abdu',
 'ab

**[ Hindi ] Target Words In sorted order :::**


In [51]:
target_words = sorted(list(all_hindi_words))
target_words


['START_',
 '_END',
 '°',
 '°क',
 '°तक',
 '±',
 '³',
 '·',
 'º',
 'ºघूम',
 '́',
 '́́',
 '̃',
 '̄̄',
 '̈',
 '̈सकें',
 'μ',
 'القرآن',
 'ं',
 'ंं',
 'ंंएम',
 'ंंष्',
 'ंअइन्लिने',
 'ंअइलिन्ग्',
 'ंअकेर्',
 'ंअटेर्निट्य्',
 'ंआ',
 'ंइल्टोन्',
 'ंइस',
 'ंईश्थ्',
 'ंउस्ट्',
 'ंएअस्लेस्',
 'ंएडिचल्',
 'ंओटोर्',
 'ंओरि',
 'ंओरेचम्बे',
 'ंख्',
 'ंग्रहालय',
 'ंड़ा',
 'ंण्',
 'ंबं',
 'ंमीसल्स्',
 'ंष्ठ्फ्',
 'ंसबंध',
 'ः',
 'ःं',
 'ःःःःःःःः',
 'ःअर्डिए',
 'ःऊघ्',
 'ःएअल्ट्हऋ',
 'ःएअल्ट्ह्',
 'ःएल्प्',
 'ःओउसिन्ग्',
 'ःओउसे',
 'ःओमे',
 'ःग्',
 'ःघ्',
 'ःछ्',
 'ःण्',
 'ःशै',
 'ःष्फ्',
 'ःहृ',
 'अ',
 'अँ',
 'अँगुली',
 'अँग्रेज़ी',
 'अँग्रेजी',
 'अँधकारयुग',
 'अँधेरा',
 'अँधेरी',
 'अँधेरे',
 'अँन्टीनॅटल',
 'अँसेस्',
 'अंक',
 'अंकगणित',
 'अंकन',
 'अंकल',
 'अंकलों',
 'अंकित',
 'अंकीय',
 'अंकुर',
 'अंकुरित',
 'अंकुश',
 'अंकों',
 'अंकोर',
 'अंखड़ित',
 'अंग',
 'अंगअंग',
 'अंगच्छेदन',
 'अंगद',
 'अंगमारी',
 'अंगरक्षक',
 'अंगरक्षकः',
 'अंगरखा',
 'अंगरेजी',
 'अंगारे',
 'अंगीकार',
 'अंगीकृत',
 'अंगीरा',
 'अं

***Tokens***

In [52]:
num_encoder_tokens_E = len(input_words)
num_encoder_tokens_E

38582

In [53]:
num_decoder_tokens_H = len(target_words)
num_decoder_tokens_H


44333

In [ ]:
num_decoder_tokens_H += 1 #for zero padding


In [54]:
num_encoder_tokens_E,num_decoder_tokens_H

(38582, 44333)

Encoder Tokens [ English ] : 12083 <br>
Decoder Tokens [ Hindi   ] :14465

***Indexing For Tokens***

In [55]:
input_token_index = dict([(word,i+1) for i ,word in enumerate(input_words)])

In [56]:
target_token_index = dict([(word,i+1) for i,word in enumerate(target_words)])

In [57]:
print("Input : {} And Target : {}".format(input_token_index,target_token_index))

Input : {'a': 1, 'aa': 2, 'aaa': 3, 'aaber': 4, 'aac': 5, 'aacharan': 6, 'aachmanritually': 7, 'aact': 8, 'aadam': 9, 'aadan': 10, 'aadanthy': 11, 'aadh': 12, 'aadi': 13, 'aadimindian': 14, 'aadiparva': 15, 'aaee': 16, 'aaeene': 17, 'aag': 18, 'aagara': 19, 'aah': 20, 'aai': 21, 'aaineakbari': 22, 'aaj': 23, 'aak': 24, 'aakhr': 25, 'aakrnsa': 26, 'aalekh': 27, 'aalh': 28, 'aalims': 29, 'aamar': 30, 'aamir': 31, 'aamlopi': 32, 'aananthi': 33, 'aand': 34, 'aangghchche': 35, 'aangkadoong': 36, 'aanre': 37, 'aaranyak': 38, 'aarathi': 39, 'aarati': 40, 'aareer': 41, 'aarsu': 42, 'aarthie': 43, 'aarti': 44, 'aarun': 45, 'aarya': 46, 'aathri': 47, 'aatmikaprikarmasandhiniyamageetparvdeepgeetsmarikaneelambra': 48, 'aatre': 49, 'aatri': 50, 'aawazekhalq': 51, 'aayaat': 52, 'aayat': 53, 'aayats': 54, 'aaysaar': 55, 'aazad': 56, 'aazadhind': 57, 'aazamgad': 58, 'ab': 59, 'abacha': 60, 'aback': 61, 'abacus': 62, 'abad': 63, 'abandon': 64, 'abandoned': 65, 'abandoning': 66, 'abani': 67, 'abated': 6

Reversing Index

In [58]:
Rev_input_token_index = dict([(i+1,word) for i ,word in enumerate(input_words)])

In [59]:
Rev_target_token_index = dict([(i+1,word) for i,word in enumerate(target_words)])

In [60]:
print("Input : {} And Target : {}".format(Rev_input_token_index,Rev_target_token_index))

Input : {1: 'a', 2: 'aa', 3: 'aaa', 4: 'aaber', 5: 'aac', 6: 'aacharan', 7: 'aachmanritually', 8: 'aact', 9: 'aadam', 10: 'aadan', 11: 'aadanthy', 12: 'aadh', 13: 'aadi', 14: 'aadimindian', 15: 'aadiparva', 16: 'aaee', 17: 'aaeene', 18: 'aag', 19: 'aagara', 20: 'aah', 21: 'aai', 22: 'aaineakbari', 23: 'aaj', 24: 'aak', 25: 'aakhr', 26: 'aakrnsa', 27: 'aalekh', 28: 'aalh', 29: 'aalims', 30: 'aamar', 31: 'aamir', 32: 'aamlopi', 33: 'aananthi', 34: 'aand', 35: 'aangghchche', 36: 'aangkadoong', 37: 'aanre', 38: 'aaranyak', 39: 'aarathi', 40: 'aarati', 41: 'aareer', 42: 'aarsu', 43: 'aarthie', 44: 'aarti', 45: 'aarun', 46: 'aarya', 47: 'aathri', 48: 'aatmikaprikarmasandhiniyamageetparvdeepgeetsmarikaneelambra', 49: 'aatre', 50: 'aatri', 51: 'aawazekhalq', 52: 'aayaat', 53: 'aayat', 54: 'aayats', 55: 'aaysaar', 56: 'aazad', 57: 'aazadhind', 58: 'aazamgad', 59: 'ab', 60: 'abacha', 61: 'aback', 62: 'abacus', 63: 'abad', 64: 'abandon', 65: 'abandoned', 66: 'abandoning', 67: 'abani', 68: 'abated

***Shuffle***

In [61]:
df = shuffle(df)
df.head(5)

english_sentence  \
22347  the problem is they are just too expensive ten...   
3359   in april this year the prime minister received...   
20130                        depends on one crucial fact   
35589                                     similar answer   
36510  with the help of dwanduwad islamic dharmashast...   

                                          hindi_sentence  \
22347  START_ समस्या यह है कि वो बहुत महंगे है हज़ारो...   
3359   START_ इस साल अप्रैल में प्रधानमंत्री को अपनी ...   
20130  START_ एक अत्यंत महत्त्वपूर्ण बात पर निर्भर कर...   
35589                          START_ सामान्य अन्तर _END   
36510  START_ द्वंद्ववाद की मदद से इस्लामी धर्मशास्त्...   

       Length of English Sentences  Length of Hindi Sentences  
22347                           13                         12  
3359                            17                         17  
20130                            5                         10  
35589                            2                          4  
36510                           14                         17

***Train & Test Split Data***

In [62]:
X,Y = df["english_sentence"],df['hindi_sentence']

In [63]:
x_train,x_test,y_train,y_test = train_test_split(X,Y,test_size=0.3,random_state=30)

In [64]:
x_train.shape,y_train.shape

((18036,), (18036,))

In [65]:
x_test.shape,y_test.shape

((7731,), (7731,))

***Save The Data in Pickle Format***

In [66]:
x_train.to_pickle('x_train.pkl')
x_test.to_pickle('x_test.pkl')
y_train.to_pickle('y_train.pkl')
y_test.to_pickle('y_test.pkl')

**Generating The Batches For DataSet**

Samples

In [67]:
np.zeros((128,20),dtype='float32')

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [68]:
np.zeros((128,20,14446),dtype='float32')

array([[[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       ...,

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0.

Let's Start's The Batches

In [69]:
def generate_batch(X =x_train,Y=y_train,batch_size=128):
  while True:
    for j in range(0,len(X),batch_size):

      #------------------     Layers Creation   ----------------------------- 
      encoder_input_data=np.zeros((batch_size,max_length_source),dtype='float32')
      #128 Rows & 20 Columns

      decoder_input_data = np.zeros((batch_size,max_length_target),dtype='float32')
      #128 Rows & 20 Columns

      decoder_target_data = np.zeros((batch_size,max_length_target,num_decoder_tokens_H),dtype='float32')
      # It is Three Dimensional [128 Rows and 20 Columns] * 14446

      # first Iteration code logic i=0, [English Sentences]Good......., [Hindi Sentences]Aacha(Hindi)........ zip(X[0:0+128],Y[0:0+128])
      for i,(input_text,target_text) in enumerate(zip(X[j:j+batch_size],Y[j:j+batch_size])):
        # Hers English Words Separated
        for t,word in enumerate(input_text.split()):
          # Above we created Encode_Input_Data layer we are including that word index into layer
          encoder_input_data[i,t] = input_token_index[word]
          #It is Example : For First Iteration encoder_input_data[0,0] =1256

        for t,word in enumerate(target_text.split()):
          # Above we created Decoder_Input_Data layer we are including that word index into layer
          if  t<len(target_text.split()) -1:
            decoder_input_data[i,t] = target_token_index[word]
          if t>0:
            # Decoder Target like a decoder if word presented if represented 1 else 0
            # we are Keepig t>0 because we don't need START
            decoder_target_data[i,t-1,target_token_index[word]]=1
            # Above We Mention Three values ! Rember Decoder_Target_Data is 3 Dimensional
        yield([encoder_input_data,decoder_input_data],decoder_target_data)

**Encoder & Decoder Architecture**

Before Going Main Architecture Let Parctice Some Normal Things Ok!

In [70]:
data = np.array([[1,2,0,0]])
data.shape
#One Row And 4 Columns

(1, 4)

In [71]:
# Let's Build Small Example Model

In [72]:
x = Input(shape=(None,))
e = Embedding(5,5,mask_zero=True)(x)
m = Model(inputs=x,outputs=e)
p =m.predict(data)

In [73]:
print(p.shape)

(1, 4, 5)


In [74]:
print(p)

[[[ 0.01228404  0.00808271  0.04648527  0.00110035  0.02664003]
  [-0.01957023 -0.02899926  0.01669905 -0.04600201 -0.00611962]
  [-0.01468407  0.03634665 -0.04621065 -0.04093482 -0.0029062 ]
  [-0.01468407  0.03634665 -0.04621065 -0.04093482 -0.0029062 ]]]


***Let's Start Buliding Encoder***

In [75]:
length_dimesnion = 300  

In [76]:
# By Using Kera's we doing this 
encoder_inputs = Input(shape=(None,))
encoder_embedding = Embedding(num_encoder_tokens_E,length_dimesnion,mask_zero=True)(encoder_inputs)
encoder_lstm = LSTM(length_dimesnion,return_state=True)

encoder_outputs,hidden_state,cell_state = encoder_lstm(encoder_embedding)
# We Don't Need encoder_outputs present so we discard it
encoder_states = [hidden_state,cell_state]

***Let's Start Buliding Decoder***

In [77]:
decoder_inputs = Input(shape=(None,))
decoder_embedding = Embedding(num_decoder_tokens_H,length_dimesnion,mask_zero=True)
dec_emb = decoder_embedding(decoder_inputs)
decoder_lstm = LSTM(length_dimesnion,return_sequences=True,return_state=True)

#Here We don't need d_hidden_state,d_cell_state
decoder_outputs,d_hidden_state,d_cell_state = decoder_lstm(dec_emb,initial_state=encoder_states)

# Adding Dense Layer
decoder_dense = Dense(num_decoder_tokens_H,activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)


***MODEL***

In [78]:
model = Model([encoder_inputs,decoder_inputs],decoder_outputs)

In [79]:
model.compile(optimizer='adam', loss='categorical_crossentropy',metrics=['accuracy'])

In [80]:
model.summary()

Model: "model_1"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_2 (InputLayer)           [(None, None)]       0           []                               
                                                                                                  
 input_3 (InputLayer)           [(None, None)]       0           []                               
                                                                                                  
 embedding_1 (Embedding)        (None, None, 300)    11574600    ['input_2[0][0]']                
                                                                                                  
 embedding_2 (Embedding)        (None, None, 300)    13299900    ['input_3[0][0]']                
                                                                                            

***Training Model***

In [81]:
train_samples = len(x_train)
test_samples = len(x_test)
batch_size = 128
epochs = 100

In [82]:
model.fit_generator(generator = generate_batch(x_train, y_train, batch_size = batch_size),
                    steps_per_epoch = train_samples//batch_size,
                    epochs=100,
                    validation_data = generate_batch(x_test, y_test, batch_size = batch_size),
                    validation_steps = test_samples//batch_size)



/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:5: UserWarning: `Model.fit_generator` is deprecated and will be removed in a future version. Please use `Model.fit`, which supports generators.
  """


Epoch 1/100
140/140 [==============================] - 101s 651ms/step - loss: 1.4336 - accuracy: 0.1142 - val_loss: 1.1271 - val_accuracy: 0.1183
Epoch 2/100
140/140 [==============================] - 85s 605ms/step - loss: 1.1219 - accuracy: 0.1934 - val_loss: 3.0425 - val_accuracy: 0.1124
Epoch 3/100
140/140 [==============================] - 85s 611ms/step - loss: 0.8195 - accuracy: 0.4749 - val_loss: 1.2883 - val_accuracy: 0.1106
Epoch 4/100
140/140 [==============================] - 90s 645ms/step - loss: 0.6126 - accuracy: 0.6894 - val_loss: 2.9561 - val_accuracy: 0.1173
Epoch 5/100
140/140 [==============================] - 88s 629ms/step - loss: 0.4196 - accuracy: 0.7938 - val_loss: 1.4802 - val_accuracy: 0.1155
Epoch 6/100
140/140 [==============================] - 85s 611ms/step - loss: 0.3828 - accuracy: 0.8166 - val_loss: 2.6379 - val_accuracy: 0.1292
Epoch 7/100
140/140 [==============================] - 85s 610ms/step - loss: 0.3192 - accuracy: 0.8498 - val_loss: 1.7278 

In [83]:
model.save_weights('weights.h5')

In [85]:
# Encoder Input Sequence thorugh the vectors
encoder_model = Model(encoder_inputs,encoder_states)


# Decoder 
decoder_state_input_h = Input(shape = (length_dimesnion,))
decoder_state_input_c = Input(shape =(length_dimesnion,))

decoder_states_inputs =[decoder_state_input_h,decoder_state_input_c]

decoder_embedding2 = decoder_embedding(decoder_inputs)
decoder_outputs2, state_h2, state_c2 = decoder_lstm(decoder_embedding2,initial_state = decoder_states_inputs)
decoder_states2 = [state_h2, state_c2]
decoder_outputs2 = decoder_dense(decoder_outputs2) # Dense Softmax layer


#Final  DECODER MODEL
decoder_Model = Model([decoder_inputs]+decoder_states_inputs,
                      [decoder_outputs2]+decoder_states2)

In [86]:
def decode_sequence(input_seq):
    # Encode the input as state vectors.
    states_value = encoder_model.predict(input_seq)
    # Generate empty target sequence of length 1.
    target_seq = np.zeros((1,1))
    # Populate the first character of target sequence with the start character.
    target_seq[0, 0] = target_token_index['START_']

    # Sampling loop for a batch of sequences
    # (to simplify, here we assume a batch of size 1).
    stop_condition = False
    decoded_sentence = ''
    while not stop_condition:
        output_tokens, h, c = decoder_Model.predict([target_seq] + states_value)

        # Sample a token
        sampled_token_index = np.argmax(output_tokens[0, -1, :])
        sampled_char = Rev_target_token_index[sampled_token_index]
        decoded_sentence += ' '+sampled_char

        # Exit condition: either hit max length
        # or find stop character.
        if (sampled_char == '_END' or
           len(decoded_sentence) > 50):
            stop_condition = True

        # Update the target sequence (of length 1).
        target_seq = np.zeros((1,1))
        target_seq[0, 0] = sampled_token_index

        # Update states
        states_value = [h, c]

    return decoded_sentence


In [87]:
train_gen = generate_batch(x_train, y_train, batch_size = 1)
k=-1

In [89]:
k+=1
(input_seq, actual_output), _ = next(train_gen)
decoded_sentence = decode_sequence(input_seq)
print('Input English sentence:', x_train[k:k+1].values[0])
print('Actual Hindi Translation:', y_train[k:k+1].values[0][6:-4])
print('Predicted Hindi Translation:', decoded_sentence[:-4])

Input English sentence: which has simply pegged certain emotional rewards
Actual Hindi Translation:  हमने अपने आप को कुछ ऐसे भावनात्मक सुखों से जोड़ रखा है 
Predicted Hindi Translation:  लेकिन कि इस पर अनुवाद हों तो जैसे 


In [91]:
k+=1
(input_seq, actual_output), _ = next(train_gen)
decoded_sentence = decode_sequence(input_seq)
print('Input English sentence:', x_train[k:k+1].values[0])
print('Actual Hindi Translation:', y_train[k:k+1].values[0][6:-4])
print('Predicted Hindi Translation:', decoded_sentence[:-4])

Input English sentence: the other day i was in kerala my home state
Actual Hindi Translation:  कुछ दिनों पहले मैं केरल गया हुआ था मेरे गाँव 
Predicted Hindi Translation:  लेकिन कुछ ऐसी अविश्वसनीय कि द्रव आपने आपने और व
